# Hafta 7: Üretim Ortamında Model İzleme ve Sürekli Teslimat (CD)

**Dersin Hedefleri:**
1.  Bir makine öğrenmesi modelinin performansının zamanla neden düştüğünü (model degradation) anlamak.
2.  Veri Kayması (Data Drift) ve Kavram Kayması (Concept Drift) arasındaki farkı kavramak.
3.  Üretimdeki bir modelin hem operasyonel hem de performans metriklerini izlemek için stratejiler öğrenmek.
4.  Veri kaymasını tespit etmek için istatistiksel yöntemler uygulamak.
5.  Sürekli Teslimat/Dağıtım (Continuous Delivery/Deployment) kavramını ve MLOps döngüsünü nasıl tamamladığını anlamak.

## 1. Neden Modeller Zamanla "Eskir"?

Bir modeli eğitip dağıttığınızda, o model, eğitim verisinin temsil ettiği "dünyanın anlık bir fotoğrafı" üzerine kuruludur. Ancak dünya statik değildir.

- **Veri Kayması (Data Drift):** Üretim ortamına gelen verinin istatistiksel özellikleri (örn: ortalama, dağılım), modelin eğitildiği veriden zamanla farklılaşmaya başlar. **Örnek:** Ekonomik bir kriz sonrası, insanların ortalama geliri düşebilir. Modeliniz "gelir" özelliğine dayanıyorsa, performansı düşecektir. Modelin kendisi hala doğrudur, ancak girdi verisi değişmiştir.
- **Kavram Kayması (Concept Drift):** Verideki özellikler ile hedef değişken arasındaki temel ilişki değişir. Bu daha nadir ama daha ciddi bir sorundur. **Örnek:** Bir spam tespit modelinde, "ücretsiz" kelimesi başlangıçta güçlü bir spam göstergesiyken, zamanla spam gönderenlerin yeni taktikler geliştirmesiyle bu kelimenin önemi azalabilir. Aynı girdi, artık farklı bir anlama gelmektedir.

Bu nedenlerle, dağıtılan bir modeli "kur ve unut" yaklaşımıyla bırakmak, kaçınılmaz olarak performans düşüşüne ve yanlış kararlara yol açar.

## 2. İzlenmesi Gerekenler Nelerdir?

### a) Operasyonel Metrikler (Sistem Sağlığı)
Bunlar, model API'mizin bir yazılım olarak ne kadar sağlıklı çalıştığını gösterir.
- **Gecikme Süresi (Latency):** Bir tahmin isteğine cevap vermek ne kadar sürüyor?
- **Trafik (Throughput):** Saniyede kaç istek karşılanıyor?
- **Hata Oranı (Error Rate):** İsteklerin yüzde kaçı 500 gibi sunucu hatalarıyla sonuçlanıyor?
- **Kaynak Kullanımı:** CPU, bellek, disk kullanımı ne durumda?

### b) Model Performans Metrikleri (Tahmin Kalitesi)
Bunlar, modelin tahminlerinin ne kadar doğru olduğunu gösterir. Bunun için "ground truth" (gerçek etiketler) gereklidir, ki bu her zaman anında mevcut olmayabilir.
- **Accuracy, Precision, Recall, F1-Score, ROC AUC** gibi metriklerin zaman içindeki değişimi.

### c) Veri Kayması Metrikleri (Veri Sağlığı)
Ground truth olmadığında bile, modelin performansının düşebileceğine dair erken bir uyarı sistemi olarak çalışırlar.
- **Girdi Veri Dağılımı:** Üretimdeki verinin sayısal özelliklerinin (ortalama, standart sapma, min, max) eğitim verisinden ne kadar saptığı.
- **Kategorik Veri Dağılımı:** Kategorik özelliklerin frekanslarının değişip değişmediği.

## 3. Pratik Uygulama: Veri Kaymasını Tespit Etme

Bu bölümde, bir modelin eğitildiği "referans" veri seti ile zamanla gelen "üretim" veri seti arasında bir kayma olup olmadığını istatistiksel olarak nasıl tespit edebileceğimizi göreceğiz.

**Yöntem:** Sayısal iki örneklemin (referans ve üretim) aynı dağılımdan gelip gelmediğini test eden **Kolmogorov-Smirnov (K-S) testini** kullanacağız.
- **Null Hipotezi (H0):** İki örneklem aynı dağılımdan gelmektedir (kayma yok).
- **Test Sonucu:** Testin p-değeri, belirlediğimiz bir anlamlılık seviyesinden (örn: 0.05) küçükse, H0 hipotezini reddederiz ve **"İki dağılım arasında istatistiksel olarak anlamlı bir fark vardır, yani veri kayması tespit edilmiştir"** deriz.

**Kurulum:**
```bash
pip install scipy
```

from scipy.stats import ks_2samp

def check_drift(reference_series, production_series, feature_name, alpha=0.05):
    """
    K-S testi kullanarak veri kaymasını tespit eder.
    
    Parameters:
    -----------
    reference_series : pd.Series
        Referans (eğitim) verisi
    production_series : pd.Series
        Üretim verisi
    feature_name : str
        Özellik adı
    alpha : float
        Anlamlılık seviyesi (varsayılan: 0.05)
    
    Returns:
    --------
    bool : Kayma tespit edildiyse True, edilmediyse False
    """
    ks_statistic, p_value = ks_2samp(reference_series, production_series)
    
    print(f"\n{'='*60}")
    print(f"  {feature_name} için Veri Kayması Analizi")
    print(f"{'='*60}")
    print(f"K-S İstatistiği: {ks_statistic:.4f}")
    print(f"P-Değeri:        {p_value:.4f}")
    print(f"Anlamlılık:      α = {alpha}")
    print(f"{'-'*60}")
    
    if p_value < alpha:
        print(f"✗ SONUÇ: VERİ KAYMASI TESPİT EDİLDİ (p={p_value:.4f} < {alpha})")
        print(f"  Null hipotez reddedildi.")
        print(f"  İki dağılım istatistiksel olarak farklıdır.")
        return True
    else:
        print(f"✓ SONUÇ: Anlamlı bir kayma YOK (p={p_value:.4f} ≥ {alpha})")
        print(f"  Null hipotez reddedilemedi.")
        print(f"  İki dağılım benzerdir.")
        return False

# Testleri çalıştır
print("TEST 1: Normal Üretim Verisi (Kayma Beklenmez)")
check_drift(reference_data['temperature'], production_data_ok['temperature'], 
            'Sıcaklık (Normal Durum)')

print("\n\nTEST 2: Kayma Olan Üretim Verisi (Kayma Beklenir)")
check_drift(reference_data['temperature'], production_data_drifted['temperature'], 
            'Sıcaklık (Kayma Durumu)')

## 4. Sürekli Teslimat/Dağıtım (CI/CD)

CI (Sürekli Entegrasyon) kodun kalitesini kontrol eder. CD ise bu kaliteli kodun (veya modelin) üretim ortamına otomatik olarak dağıtılmasını sağlar.

**Basitleştirilmiş bir MLOps CD Pipeline'ı:**

1.  Bir veri bilimci, yeni verilerle veya daha iyi bir teknikle eğittiği yeni bir modeli `MLflow`'a kaydeder.
2.  Bu yeni model, bir "hazırlık" (staging) ortamında bir dizi otomatik teste tabi tutulur:
    *   Modelin performansı, mevcut üretimdeki modelden daha mı iyi?
    *   Modelin tahmin gecikmesi kabul edilebilir sınırlar içinde mi?
    *   Model, bilinen kritik veri örnekleri (edge cases) için mantıklı tahminler üretiyor mu?
3.  Tüm testler başarılı olursa, bir yetkilinin onayıyla (Sürekli Teslimat) veya tamamen otomatik olarak (Sürekli Dağıtım), yeni model, üretimdeki eski modelin yerini alır.

Bu döngü, MLOps'un son halkasıdır ve ML sistemlerinin sürekli olarak öğrenmesini ve iyileşmesini sağlar.

### Alıştırma Özeti

**Öğrenilen Konular:**

1. **Veri Analizi Otomasyonu:**
   - `select_dtypes()` ile veri tiplerini filtreleme
   - DataFrame iteration ile dinamik analiz
   - Liste comprehension ile veri yapıları oluşturma

2. **İstatistiksel Test Uygulaması:**
   - K-S testini programatik olarak uygulama
   - P-değerlerini yorumlama
   - Çoklu test senaryolarını otomatikleştirme

3. **Veri Görselleştirme:**
   - Çoklu subplot'lar ile dashboard oluşturma
   - Koşullu renklendirme (drift detected → red, else → green)
   - Bar charts, pie charts ile özet bilgi sunma

4. **Production-Ready Kod:**
   - Kapsamlı docstring yazımı
   - Error handling (sütun kontrolü)
   - Okunabilir output formatı

**Gerçek Dünya Kullanımı:**
Bu rapor günlük/haftalık cron job ile çalıştırılarak:
- Email ile takımlara gönderilebilir
- Dashboard'a yüklenebilir
- Otomatik uyarı sistemlerine bağlanabilir
- Model yeniden eğitim pipeline'ını tetikleyebilir

fig, axes = plt.subplots(2, 2, figsize=(16, 10))

# Grafik 1: P-değerleri
ax1 = axes[0, 0]
colors = ['red' if x else 'green' for x in monitoring_report['drift_detected']]
ax1.barh(monitoring_report['feature_name'], monitoring_report['ks_p_value'], color=colors, alpha=0.7)
ax1.axvline(x=0.05, color='black', linestyle='--', linewidth=2, label='α = 0.05 (Eşik)')
ax1.set_xlabel('P-Değeri', fontsize=12)
ax1.set_ylabel('Özellik', fontsize=12)
ax1.set_title('K-S Testi P-Değerleri', fontsize=14, fontweight='bold')
ax1.legend()
ax1.grid(alpha=0.3)

# Grafik 2: Ortalama Farkları (%)
ax2 = axes[0, 1]
colors = ['red' if x else 'green' for x in monitoring_report['drift_detected']]
ax2.barh(monitoring_report['feature_name'], monitoring_report['mean_diff_pct'], color=colors, alpha=0.7)
ax2.axvline(x=0, color='black', linestyle='-', linewidth=1)
ax2.set_xlabel('Ortalama Farkı (%)', fontsize=12)
ax2.set_ylabel('Özellik', fontsize=12)
ax2.set_title('Referans vs Üretim: Ortalama Farkı', fontsize=14, fontweight='bold')
ax2.grid(alpha=0.3)

# Grafik 3: K-S İstatistiği
ax3 = axes[1, 0]
colors = ['red' if x else 'green' for x in monitoring_report['drift_detected']]
ax3.barh(monitoring_report['feature_name'], monitoring_report['ks_statistic'], color=colors, alpha=0.7)
ax3.set_xlabel('K-S İstatistiği', fontsize=12)
ax3.set_ylabel('Özellik', fontsize=12)
ax3.set_title('Kolmogorov-Smirnov İstatistikleri', fontsize=14, fontweight='bold')
ax3.grid(alpha=0.3)

# Grafik 4: Kayma Durumu (Pie Chart)
ax4 = axes[1, 1]
drift_summary = monitoring_report['drift_detected'].value_counts()
colors_pie = ['#ff6b6b', '#51cf66']
labels = ['Kayma Tespit Edildi', 'Kayma Yok']
if True in drift_summary.index and False in drift_summary.index:
    ax4.pie([drift_summary[True], drift_summary[False]], 
            labels=labels, autopct='%1.1f%%', colors=colors_pie, startangle=90)
elif True in drift_summary.index:
    ax4.pie([drift_summary[True]], labels=['Kayma Tespit Edildi'], 
            autopct='%1.1f%%', colors=['#ff6b6b'], startangle=90)
else:
    ax4.pie([drift_summary[False]], labels=['Kayma Yok'], 
            autopct='%1.1f%%', colors=['#51cf66'], startangle=90)
ax4.set_title('Genel Kayma Durumu', fontsize=14, fontweight='bold')

plt.tight_layout()
plt.show()

### Adım 4: Görsel Rapor Oluşturma

İzleme raporunu görselleştirerek daha anlaşılır hale getirelim.

print("="*80)
print(" " * 25 + "VERİ SAĞLIĞI İZLEME RAPORU")
print("="*80)
print(f"Referans Veri Boyutu: {len(reference_data)}")
print(f"Üretim Veri Boyutu:   {len(production_data_drifted)}")
print(f"Anlamlılık Seviyesi:  α = 0.05")
print("="*80)

# Raporu göster
display(monitoring_report)

# Özet istatistikler
print("\n" + "="*80)
print(" " * 30 + "ÖZET")
print("="*80)
drift_count = monitoring_report['drift_detected'].sum()
total_features = len(monitoring_report)
print(f"Toplam Özellik Sayısı:        {total_features}")
print(f"Kayma Tespit Edilen Özellik:  {drift_count}")
print(f"Kayma Yüzdesi:                {(drift_count/total_features)*100:.1f}%")

if drift_count > 0:
    print(f"\n⚠️  UYARI: {drift_count} özellikte veri kayması tespit edildi!")
    print("   Modelin performansı etkilenebilir. Aşağıdaki aksiyonlar önerilir:")
    print("   1. Modeli yeni verilerle yeniden eğitin")
    print("   2. Özellik mühendisliği stratejisini gözden geçirin")
    print("   3. Veri toplama sürecini inceleyin")
else:
    print("\n✓ Tüm özellikler normal dağılım aralığında.")

### Adım 3: Raporu Görüntüleme ve Yorumlama

def generate_monitoring_report(ref_df, prod_df, alpha=0.05):
    """
    Referans ve üretim veri setleri arasında veri kaymasını tespit eden rapor oluşturur.
    """
    report_data = []
    
    # 1. Sadece sayısal sütunları al
    numeric_cols = ref_df.select_dtypes(include=[np.number]).columns
    
    # 2. Her sayısal sütun için analiz yap
    for col in numeric_cols:
        # Sütun her iki veri setinde de var mı kontrol et
        if col not in prod_df.columns:
            print(f"Uyarı: '{col}' sütunu üretim verisinde bulunamadı. Atlanıyor...")
            continue
        
        # İstatistikleri hesapla
        ref_mean = ref_df[col].mean()
        prod_mean = prod_df[col].mean()
        mean_diff = prod_mean - ref_mean
        mean_diff_pct = (mean_diff / ref_mean) * 100 if ref_mean != 0 else np.inf
        
        # K-S testi uygula
        ks_stat, p_value = ks_2samp(ref_df[col], prod_df[col])
        drift_detected = p_value < alpha
        
        # Rapor satırını oluştur
        report_data.append({
            "feature_name": col,
            "reference_mean": ref_mean,
            "production_mean": prod_mean,
            "mean_diff": mean_diff,
            "mean_diff_pct": mean_diff_pct,
            "ks_statistic": ks_stat,
            "ks_p_value": p_value,
            "drift_detected": drift_detected
        })
    
    # 3. DataFrame olarak döndür
    report_df = pd.DataFrame(report_data)
    
    # 4. Okunabilirlik için sırala (kayma olanlar önce)
    report_df = report_df.sort_values('drift_detected', ascending=False)
    
    return report_df

# Fonksiyonu test et
print("İzleme Raporu Oluşturuluyor...")
monitoring_report = generate_monitoring_report(reference_data, production_data_drifted)
print("\n✓ Rapor oluşturuldu!")

### Adım 2: Fonksiyon İmplementasyonu

Şimdi fonksiyonu adım adım implemente edelim:

def generate_monitoring_report(ref_df, prod_df, alpha=0.05):
    """
    Referans ve üretim veri setleri arasında veri kaymasını tespit eden rapor oluşturur.
    
    Parameters:
    -----------
    ref_df : pd.DataFrame
        Referans (eğitim) veri seti
    prod_df : pd.DataFrame
        Üretim veri seti
    alpha : float, default=0.05
        İstatistiksel anlamlılık seviyesi
    
    Returns:
    --------
    pd.DataFrame
        Her özellik için kayma raporunu içeren DataFrame:
        - feature_name: Özellik adı
        - reference_mean: Referans verisinin ortalaması
        - production_mean: Üretim verisinin ortalaması
        - mean_diff: Ortalama farkı (üretim - referans)
        - mean_diff_pct: Ortalama farkı yüzdesi
        - ks_statistic: K-S test istatistiği
        - ks_p_value: K-S test p-değeri
        - drift_detected: Kayma tespit edildi mi (bool)
    
    Example:
    --------
    >>> report = generate_monitoring_report(train_data, production_data)
    >>> print(report[report['drift_detected'] == True])
    """
    pass  # Aşağıda tamamlanacak

import matplotlib.pyplot as plt
import seaborn as sns

fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(16, 6))

# Sol grafik: Kayma olmayan durum
sns.histplot(reference_data['temperature'], ax=ax1, color='blue', 
             label='Referans', kde=True, stat='density', alpha=0.5)
sns.histplot(production_data_ok['temperature'], ax=ax1, color='green', 
             label='Üretim (Normal)', kde=True, stat='density', alpha=0.5)
ax1.set_title('Sıcaklık Dağılımı: Kayma YOK', fontsize=14, fontweight='bold')
ax1.set_xlabel('Sıcaklık (°C)')
ax1.set_ylabel('Yoğunluk')
ax1.legend()
ax1.grid(alpha=0.3)

# Sağ grafik: Kayma olan durum
sns.histplot(reference_data['temperature'], ax=ax2, color='blue', 
             label='Referans', kde=True, stat='density', alpha=0.5)
sns.histplot(production_data_drifted['temperature'], ax=ax2, color='red', 
             label='Üretim (KAYMA)', kde=True, stat='density', alpha=0.5)
ax2.set_title('Sıcaklık Dağılımı: CİDDİ KAYMA', fontsize=14, fontweight='bold')
ax2.set_xlabel('Sıcaklık (°C)')
ax2.set_ylabel('Yoğunluk')
ax2.legend()
ax2.grid(alpha=0.3)

plt.tight_layout()
plt.show()

### Adım 3: Dağılımları Görselleştirme

Veri kaymasını görsel olarak anlamak için histogram ve KDE (Kernel Density Estimation) grafiklerini kullanacağız.

In [ ]:
# Üretim Verisi 1: Kayma YOK (parametreler çok benzer)
production_data_ok = pd.DataFrame({
    'temperature': np.random.normal(loc=25.5, scale=5.2, size=500),
    'pressure': np.random.normal(loc=101.2, scale=1.1, size=500)
})

# Üretim Verisi 2: CİDDİ KAYMA (sıcaklık ortalaması 10 derece arttı)
production_data_drifted = pd.DataFrame({
    'temperature': np.random.normal(loc=35, scale=6, size=500),
    'pressure': np.random.normal(loc=101.0, scale=1.2, size=500)
})

print("Üretim Verisi (Normal) - İstatistikler:")
print(production_data_ok.describe())
print("\n\nÜretim Verisi (Kayma) - İstatistikler:")
print(production_data_drifted.describe())

### Adım 2: Üretim Verileri Oluşturma

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from scipy.stats import ks_2samp

# --- 1. Sentetik Veri Üretimi ---
# a) Referans Veri (Modelin eğitildiği veri)
np.random.seed(42)
reference_data = pd.DataFrame({
    'temperature': np.random.normal(loc=25, scale=5, size=1000),
    'pressure': np.random.normal(loc=101.3, scale=1, size=1000)
})

# b) Üretim Verisi 1 (Kayma Yok)
production_data_ok = pd.DataFrame({
    'temperature': np.random.normal(loc=25.5, scale=5.2, size=500), # Hafif, önemsiz değişiklik
    'pressure': np.random.normal(loc=101.2, scale=1.1, size=500)
})

# c) Üretim Verisi 2 (Ciddi Kayma Var)
# Sıcaklıkların ortalaması yaz mevsimi nedeniyle belirgin şekilde artmış olsun.
production_data_drifted = pd.DataFrame({
    'temperature': np.random.normal(loc=35, scale=6, size=500), # Ortalamada ciddi kayma
    'pressure': np.random.normal(loc=101.0, scale=1.2, size=500)
})

# --- 2. Veri Dağılımlarını Görselleştirme ---
fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(16, 6), sharey=True)

# Grafik 1: Kayma Olmayan Durum
sns.histplot(reference_data['temperature'], ax=ax1, color='blue', label='Referans', kde=True, stat='density')
sns.histplot(production_data_ok['temperature'], ax=ax1, color='green', label='Üretim (OK)', kde=True, stat='density')
ax1.set_title('Sıcaklık Dağılımı (Kayma Yok)')
ax1.legend()

# Grafik 2: Kayma Olan Durum
sns.histplot(reference_data['temperature'], ax=ax2, color='blue', label='Referans', kde=True, stat='density')
sns.histplot(production_data_drifted['temperature'], ax=ax2, color='red', label='Üretim (Kayma Var)', kde=True, stat='density')
ax2.set_title('Sıcaklık Dağılımı (CİDDİ KAYMA)')
ax2.legend()

plt.show()

# --- 3. İstatistiksel Test ile Kaymayı Tespit Etme ---
def check_drift(reference_series, production_series, feature_name, alpha=0.05):
    """
    Performs the K-S test to check for data drift between two series.
    """
    ks_statistic, p_value = ks_2samp(reference_series, production_series)
    
    print(f"\n--- {feature_name} için Kayma Testi ---")
    print(f"K-S İstatistiği: {ks_statistic:.4f}")
    print(f"P-Değeri: {p_value:.4f}")
    
    if p_value < alpha:
        print(f"Sonuç: Hipotez reddedildi. Veri kayması TESPİT EDİLDİ (p < {alpha}).")
        return True
    else:
        print(f"Sonuç: Hipotez reddedilemedi. Anlamlı bir veri kayması YOK (p >= {alpha}).")
        return False

# Testleri çalıştır
check_drift(reference_data['temperature'], production_data_ok['temperature'], 'Sıcaklık (Durum OK)')
check_drift(reference_data['temperature'], production_data_drifted['temperature'], 'Sıcaklık (Durum KAYMA)')

## 4. Sürekli Teslimat/Dağıtım (CI/CD)

CI (Sürekli Entegrasyon) kodun kalitesini kontrol eder. CD ise bu kaliteli kodun (veya modelin) üretim ortamına otomatik olarak dağıtılmasını sağlar.

**Basitleştirilmiş bir MLOps CD Pipeline'ı:**

1.  Bir veri bilimci, yeni verilerle veya daha iyi bir teknikle eğittiği yeni bir modeli `MLflow`'a kaydeder.
2.  Bu yeni model, bir "hazırlık" (staging) ortamında bir dizi otomatik teste tabi tutulur:
    *   Modelin performansı, mevcut üretimdeki modelden daha mı iyi?
    *   Modelin tahmin gecikmesi kabul edilebilir sınırlar içinde mi?
    *   Model, bilinen kritik veri örnekleri (edge cases) için mantıklı tahminler üretiyor mu?
3.  Tüm testler başarılı olursa, bir yetkilinin onayıyla (Sürekli Teslimat) veya tamamen otomatik olarak (Sürekli Dağıtım), yeni model, üretimdeki eski modelin yerini alır.

Bu döngü, MLOps'un son halkasıdır ve ML sistemlerinin sürekli olarak öğrenmesini ve iyileşmesini sağlar.

### Alıştırma: Bir İzleme Raporu Oluşturun

1.  Yukarıdaki `reference_data` ve `production_data_drifted` DataFrame'lerini kullanarak bir fonksiyon yazın.
2.  Bu fonksiyon, iki DataFrame'i almalı ve her bir sayısal sütun için (`temperature`, `pressure`) aşağıdaki bilgileri içeren bir özet `pandas.DataFrame` döndürmelidir:
    *   Sütun Adı
    *   Referans Ortalaması
    *   Üretim Ortalaması
    *   K-S Testi p-değeri
    *   `drift_detected` (True/False) adında bir sütun.
3.  Bu fonksiyonun çıktısı, bir veri bilimcinin veya operasyon ekibinin modelin sağlığını hızla değerlendirebileceği basit bir izleme raporu olacaktır.

In [ ]:
# Alıştırma için çözüm alanı
def generate_monitoring_report(ref_df, prod_df, alpha=0.05):
    report_data = []
    numeric_cols = ref_df.select_dtypes(include=np.number).columns
    
    for col in numeric_cols:
        if col in prod_df.columns:
            ks_stat, p_value = ks_2samp(ref_df[col], prod_df[col])
            drift_detected = p_value < alpha
            
            report_data.append({
                "feature_name": col,
                "reference_mean": ref_df[col].mean(),
                "production_mean": prod_df[col].mean(),
                "ks_p_value": p_value,
                "drift_detected": drift_detected
            })
            
    return pd.DataFrame(report_data)

monitoring_report = generate_monitoring_report(reference_data, production_data_drifted)
print("--- Veri Sağlığı İzleme Raporu ---")
display(monitoring_report)

### Haftanın Özeti

Bu hafta, MLOps yaşam döngüsünün son ve en kritik halkalarını tamamladık.
- Modeller statik değildir; dünya değiştikçe performansları düşer. **Veri Kayması** bu düşüşün en yaygın nedenidir.
- Üretimdeki bir modeli, hem sistem sağlığı (operasyonel metrikler) hem de veri ve tahmin kalitesi (performans ve kayma metrikleri) açısından sürekli **izlemeliyiz**.
- **İstatistiksel testler** (K-S testi gibi), veri kaymasını objektif olarak tespit etmek için güçlü araçlardır.
- **Sürekli Teslimat (CD)**, test edilmiş ve onaylanmış yeni modellerin üretim ortamına güvenli ve otomatik bir şekilde dağıtılmasını sağlayarak MLOps döngüsünü tamamlar.

### Sonraki Adımlar

Geleneksel ML sistemlerini baştan sona (versiyon kontrolünden izlemeye kadar) nasıl inşa edeceğimizi öğrendik. Artık, yapay zekanın en heyecan verici ve en güncel alanına girmeye hazırız. Bir sonraki hafta, **Hafta 8: Büyük Dil Modelleri (LLM) Temelleri ve Prompt Mühendisliği**'nde, metin anlayan, üreten ve bizimle diyalog kurabilen devasa modellerin dünyasına ilk adımımızı atacağız.

---

## **Hafta 8: Büyük Dil Modelleri (LLM) Temelleri ve Prompt Mühendisliği**
```python